<a href="https://colab.research.google.com/github/NH0917/ghg/blob/main/LAMA_openfe_v3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#!pip install openfe
!pip install -U lightautoml
#!pip install optuna
#!pip install optuna-integration[lightgbm]

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 416.4/416.4 kB 7.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.7/215.7 kB 14.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.7/98.7 MB 25.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 298.0/298.0 kB 17.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 71.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.1/12.1 MB 114.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 309.5/309.5 kB 19.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.1/10.1 MB 128.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 619.9/619.9 MB 2.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 317.1/317.1 MB 3.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.8/11.8 MB 83.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.0/21.0 MB 83.7 MB/s eta 0:00:00
  

In [ ]:
#!cat /proc/cpuinfo

In [ ]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import xgboost
#import optuna.integration.lightgbm as lgb
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import mean_absolute_error, mean_squared_log_error
#from openfe import OpenFE, transform
import io
import contextlib
#from autogluon.tabular import TabularDataset, TabularPredictor
from sklearn.preprocessing import LabelEncoder
import warnings

from lightautoml.automl.presets.tabular_presets import TabularAutoML, TabularUtilizedAutoML
from lightautoml.tasks import Task
from lightautoml.report.report_deco import ReportDeco, ReportDecoUtilized

from logging import getLogger, INFO

logger = getLogger(__name__)
logger.setLevel("WARNING")

warnings.simplefilter('ignore')

import sys

sys.path.append("/content/drive/MyDrive/signate/ghg/src/")
pd.set_option("display.max_columns",100)

#import my code
#import sub
#import plot_importance
#import train_evall_lgb

In [ ]:
class cfg:
    """Configuration class that holds hyperparameters for quicker experimenting"""
    num_folds = 30
    random_seed = 1
    n_jobs = 16
    n_features = 10

In [ ]:
train_path = "/content/drive/MyDrive/signate/ghg/exp_new/exp3/train_df_openfe_v2.csv"
test_path = "/content/drive/MyDrive/signate/ghg/exp_new/exp3/test_df_openfe_v2.csv"
sub_path = "/content/drive/MyDrive/signate/ghg/data/sample_submission.csv"

train = pd.read_csv(train_path)
test = pd.read_csv(test_path)
sub_df = pd.read_csv(sub_path,header=None)

In [ ]:
def get_rmsle(y_true: np.array, y_pred: np.array) -> np.float64:
    """
    The Root Mean Squared Log Error (RMSLE) metric

    :param y_true: The ground truth labels given in the dataset
    :param y_pred: Our predictions
    :return: The RMSLE score
    """

    return mean_squared_log_error(y_true, y_pred, squared=False)

In [ ]:
target_col = "GHG_Direct_Emissions_14_in_metric_tons"

In [ ]:
openfe_col = [x for x in train.columns if "autoFE_f" in x]
openfe_col = openfe_col[:20]
ghg_col = [x for x in train.columns if "GHG_" in x]

In [ ]:
usecol = openfe_col + ghg_col

In [ ]:
train = train[usecol]
test = test[usecol]

In [ ]:
mean_col = ['GHG_Direct_Emissions_10_in_metric_tons',
 'GHG_Direct_Emissions_11_in_metric_tons',
 'GHG_Direct_Emissions_12_in_metric_tons',
 'GHG_Direct_Emissions_13_in_metric_tons']

train["GHG_mean"] = train[mean_col].mean(axis=1)

In [ ]:
train

autoFE_f_0  autoFE_f_1  autoFE_f_2  autoFE_f_3     autoFE_f_4  \
0       0.256280    0.255598    0.257456    0.259993  233431.101399   
1       0.507320    0.506474    0.508772    0.511393  291048.083635   
2            NaN         NaN         NaN         NaN  309246.482586   
3       0.454307    0.453770    0.456725    0.462832  253298.825453   
4       0.423794    0.422544    0.425585    0.431640  195528.620358   
...          ...         ...         ...         ...            ...   
4650    0.934813    0.935415    0.935088    0.935002  972000.319990   
4651    0.619664    0.618583    0.621199    0.625700  244746.233681   
4652    0.927570    0.928104    0.927339    0.926784  451108.762721   
4653    0.241177    0.241127    0.243275    0.231108  115269.165619   
4654         NaN         NaN         NaN         NaN  309246.482586   

      autoFE_f_5  autoFE_f_6  autoFE_f_7  autoFE_f_8  autoFE_f_9  autoFE_f_10  \
0       0.251144    0.257332         2.0    0.941520    0.261719          1.0   
1       0.511156    0.509550         4.0    0.155297    0.506711        103.0   
2            NaN         NaN       226.0         NaN         NaN         27.0   
3       0.451583    0.456008         2.0    0.374243    0.454963         93.0   
4       0.420099    0.424726         4.0    0.497989    0.425645        253.0   
...          ...         ...         ...         ...         ...          ...   
4650    0.927654    0.936081         1.0    0.726422    0.934299        147.0   
4651    0.628127    0.620695         2.0    0.681538    0.619392         72.0   
4652    0.930441    0.928260        12.0    0.674709    0.934375          6.0   
4653    0.236683    0.243194         1.0    0.970289    0.241258         19.0   
4654         NaN         NaN       226.0         NaN         NaN        119.0   

      autoFE_f_11  autoFE_f_12  autoFE_f_13  autoFE_f_14  autoFE_f_15  \
0        0.540323         39.0       1146.0          0.0        320.0   
1        0.634146         39.0       1330.0          1.0       1117.0   
2             NaN         56.0       1330.0          2.0       1117.0   
3        0.554545         38.0        337.0          3.0        270.0   
4        0.392857         42.0       1330.0          3.0       1117.0   
...           ...          ...          ...          ...          ...   
4650     0.313043         38.0        731.0          7.0        672.0   
4651     0.837607         29.0        337.0          7.0        302.0   
4652     0.627119         24.0        509.0         34.0        120.0   
4653     0.420168         35.0       1330.0         72.0       1117.0   
4654          NaN         56.0        158.0          7.0        150.0   

      autoFE_f_16   autoFE_f_17  autoFE_f_18  autoFE_f_19  \
0        0.384615  28432.604277     0.252483     0.260846   
1        0.450450  30285.575537     0.510791     0.504668   
2             NaN  30285.575537          NaN          NaN   
3        0.341667  30157.237125     0.425150     0.463151   
4        0.471074  30285.575537     0.425180     0.430696   
...           ...           ...          ...          ...   
4650     0.946903  29474.734405     0.938953     0.936665   
4651     0.695652  27516.575196     0.627976     0.621636   
4652     0.716814  30388.953546     0.933333     0.928977   
4653     0.526316  30285.575537     0.243885     0.247117   
4654          NaN           NaN          NaN          NaN   

      GHG_Direct_Emissions_10_in_metric_tons  \
0                               64816.958901   
1                               55507.543666   
2                                        NaN   
3                               54811.222708   
4                               81812.306362   
...                                      ...   
4650                            54978.841280   
4651                           208375.435367   
4652                           563756.090695   
4653                            67451.225733   
4654                                     N

In [ ]:
def rmsle(y_true, y_pred):
    rmsle = np.sqrt(mean_squared_log_error(y_true, y_pred))
    return rmsle


from sklearn.model_selection import KFold

models = []


task = Task('reg',loss="rmsle",metric="rmsle",greater_is_better=False)
roles = {
    "target":target_col
}

N_FOLDS = 5
TIMEOUT = 300
N_THREADS = 8

oof_dfs = pd.DataFrame()

kf = KFold(n_splits=cfg.num_folds,shuffle=True,random_state=42)



for i,(train_idx,val_idx) in enumerate(kf.split(train)):
  train_df = train.iloc[train_idx].reset_index(drop=True)
  val_df = train.iloc[val_idx].reset_index(drop=True)

  oof_df = pd.DataFrame()

  automl = TabularAutoML(task=task,
                          timeout=TIMEOUT,
                          cpu_limit=N_THREADS,
                          reader_params={"n_jobs":N_THREADS,"cv":N_FOLDS,"random_state":123},
                          general_params = {"use_algos": [['rf','lgb','lgb_tuned','cb','cb_tuned','linear_l2']]}
                        )

  oof_pred = automl.fit_predict(train_df, roles=roles, verbose=-1)
  oof_df["predict"] = automl.predict(val_df).data[:,0]
  oof_df["target"] = val_df[target_col]
  print(rmsle(oof_df["target"],oof_df["predict"]))

  models.append(automl)

  oof_dfs = pd.concat([oof_dfs,oof_df]).reset_index(drop=True)

INFO:lightautoml.automl.presets.base:Stdout logging level is ERROR.
INFO:lightautoml.automl.presets.base:Task: reg

INFO:lightautoml.automl.presets.base:Start automl preset with listed constraints:
INFO:lightautoml.automl.presets.base:- time: 300.00 seconds
INFO:lightautoml.automl.presets.base:- CPU: 8 cores
INFO:lightautoml.automl.presets.base:- memory: 16 GB

INFO:lightautoml.reader.base:Train data shape: (4499, 30)

INFO3:lightautoml.reader.base:Feats was rejected during automatic roles guess: []
INFO:lightautoml.automl.base:Layer 1 train process start. Time left 294.80 secs
INFO:lightautoml.ml_algo.base:Start fitting Lvl_0_Pipe_0_Mod_0_RFSklearn ...
DEBUG:lightautoml.ml_algo.base:Training params: {'bootstrap': True, 'ccp_alpha': 0.0, 'max_depth': None, 'max_features': 0.75, 'max_leaf_nodes': None, 'max_samples': None, 'min_samples_leaf': 32, 'min_samples_split': 2, 'min_weight_fraction_leaf': 0.0, 'n_estimators': 500, 'n_jobs': 4, 'oob_score': False, 'random_state': 42, 'warm_start

0.7397134908842703


INFO3:lightautoml.reader.base:Feats was rejected during automatic roles guess: []
INFO:lightautoml.automl.base:Layer 1 train process start. Time left 299.73 secs
INFO:lightautoml.ml_algo.base:Start fitting Lvl_0_Pipe_0_Mod_0_RFSklearn ...
DEBUG:lightautoml.ml_algo.base:Training params: {'bootstrap': True, 'ccp_alpha': 0.0, 'max_depth': None, 'max_features': 0.75, 'max_leaf_nodes': None, 'max_samples': None, 'min_samples_leaf': 32, 'min_samples_split': 2, 'min_weight_fraction_leaf': 0.0, 'n_estimators': 500, 'n_jobs': 4, 'oob_score': False, 'random_state': 42, 'warm_start': False, 'criterion': 'squared_error'}
INFO2:lightautoml.ml_algo.base:===== Start working with fold 0 for Lvl_0_Pipe_0_Mod_0_RFSklearn =====
[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.4s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    1.7s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    4.1s
[Parallel(n_jobs=4

0.6431448254459109


INFO3:lightautoml.reader.base:Feats was rejected during automatic roles guess: []
INFO:lightautoml.automl.base:Layer 1 train process start. Time left 299.70 secs
INFO:lightautoml.ml_algo.base:Start fitting Lvl_0_Pipe_0_Mod_0_RFSklearn ...
DEBUG:lightautoml.ml_algo.base:Training params: {'bootstrap': True, 'ccp_alpha': 0.0, 'max_depth': None, 'max_features': 0.75, 'max_leaf_nodes': None, 'max_samples': None, 'min_samples_leaf': 32, 'min_samples_split': 2, 'min_weight_fraction_leaf': 0.0, 'n_estimators': 500, 'n_jobs': 4, 'oob_score': False, 'random_state': 42, 'warm_start': False, 'criterion': 'squared_error'}
INFO2:lightautoml.ml_algo.base:===== Start working with fold 0 for Lvl_0_Pipe_0_Mod_0_RFSklearn =====
[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.4s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    1.8s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    4.1s
[Parallel(n_jobs=4

...

0.7489639197175594


INFO3:lightautoml.reader.base:Feats was rejected during automatic roles guess: []
INFO:lightautoml.automl.base:Layer 1 train process start. Time left 299.69 secs
INFO:lightautoml.ml_algo.base:Start fitting Lvl_0_Pipe_0_Mod_0_RFSklearn ...
DEBUG:lightautoml.ml_algo.base:Training params: {'bootstrap': True, 'ccp_alpha': 0.0, 'max_depth': None, 'max_features': 0.75, 'max_leaf_nodes': None, 'max_samples': None, 'min_samples_leaf': 32, 'min_samples_split': 2, 'min_weight_fraction_leaf': 0.0, 'n_estimators': 500, 'n_jobs': 4, 'oob_score': False, 'random_state': 42, 'warm_start': False, 'criterion': 'squared_error'}
INFO2:lightautoml.ml_algo.base:===== Start working with fold 0 for Lvl_0_Pipe_0_Mod_0_RFSklearn =====
[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.4s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    1.9s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    4.3s
[Parallel(n_jobs=4

0.7939268526469653


INFO3:lightautoml.reader.base:Feats was rejected during automatic roles guess: []
INFO:lightautoml.automl.base:Layer 1 train process start. Time left 299.69 secs
INFO:lightautoml.ml_algo.base:Start fitting Lvl_0_Pipe_0_Mod_0_RFSklearn ...
DEBUG:lightautoml.ml_algo.base:Training params: {'bootstrap': True, 'ccp_alpha': 0.0, 'max_depth': None, 'max_features': 0.75, 'max_leaf_nodes': None, 'max_samples': None, 'min_samples_leaf': 32, 'min_samples_split': 2, 'min_weight_fraction_leaf': 0.0, 'n_estimators': 500, 'n_jobs': 4, 'oob_score': False, 'random_state': 42, 'warm_start': False, 'criterion': 'squared_error'}
INFO2:lightautoml.ml_algo.base:===== Start working with fold 0 for Lvl_0_Pipe_0_Mod_0_RFSklearn =====
[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.4s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    1.7s
[Parallel(n_jobs=4)]: Done 442 tasks      | elapsed:    4.0s
[Parallel(n_jobs=4

0.725402610601977


In [ ]:
oof_dfs.reset_index(drop=True,inplace=True)

In [ ]:
get_rmsle(oof_dfs["target"],oof_dfs["predict"])

1.3143356474322196

In [ ]:
import matplotlib.pyplot as plt
for ml in models:
  fast_fi = ml.get_feature_scores("fast")
  fast_fi.set_index('Feature')['Importance'].plot.bar(figsize = (30, 10), grid = True)
  plt.show()

AttributeError: 'NoneType' object has no attribute 'set_index'

In [ ]:
import seaborn as sns

sns.scatterplot(x="GHG_mean",y=target_col,data=train)